In [ ]:
import paramiko
import pandas as pd
from datetime import datetime
import time


def get_data(hostname, port, username, password, script_path):
    try:
        client = paramiko.SSHClient()
        client.set_missing_host_key_policy(paramiko.AutoAddPolicy())
        client.connect(hostname, port, username, password)

        stdin, stdout, stderr = client.exec_command(f'python3 {script_path}')
        output = stdout.read().decode('utf-8').strip()

        client.close()

        output_pairs = output.split(',')

        variable_values = [float(pair.split('=')[1]) for pair in output_pairs]

        variable1, variable2, variable3 = variable_values

        return variable1, variable2, variable3

    except Exception as e:
        print(f"An error occurred: {e}")
        return None, None, None


df = pd.read_csv('Data.csv')
while True:
    try:
        temp, pressure, humidity = get_data('hostname', port, 'username', 'password', 'script_path')
        time_1 = datetime.now().time().replace(microsecond=0)
        date_1 = datetime.today().date().strftime('%d-%m-%Y')
        df_temp = pd.DataFrame(
            {'Date': [date_1], 'Time': [time_1], 'Temperature': [temp], 'Barometric Pressure': [pressure],
             'Humidity': [humidity]})
        df = pd.concat([df, df_temp])
        df.to_csv('Data.csv', index=False)
        time.sleep(59)

    except KeyboardInterrupt:
        break

df.to_csv('Data.csv', index=False)